In [1]:
# libraries

import osmnx as ox
import geopandas as gpd
import folium
import pandas as pd

In [2]:
#extract Tuaranga road geometries

G = ox.graph_from_place("Tauranga City, New Zealand", network_type='drive')

In [3]:
#import data

hybrid_services = gpd.read_file(r"C:\Users\GSE1\Beca\3813283 - PT Services and Infrastructure SSBC - Documents\Technical - Working Files\01 SSBC\05 Shortlist\01 Service options assessment\hybrid_services.geojson")
pt_demand = gpd.read_file(r'C:\Users\GSE1\Beca\3813283 - PT Services and Infrastructure SSBC - Documents\Technical - Working Files\01 SSBC\05 Shortlist\01 Service options assessment\pt_trip_2048.csv')
los_links_am = gpd.read_file(r'\\Beca.net\projects\381\3813283\4-TTR\Modelling\Outputs\Shapefiles_18Aug2023\LOS_Toll_AM_Links_2048DN_TTM22_NoSB.shp', geometry="geometry")
los_nodes_am = gpd.read_file(r'\\Beca.net\projects\381\3813283\4-TTR\Modelling\Outputs\Shapefiles_18Aug2023\LOS_Toll_AM_Nodes_2048DN_TTM22_NoSB.shp', geometry="geometry")

In [4]:
#set crs
los_links_am.set_crs('epsg:2193', inplace=True)
los_nodes_am.set_crs('epsg:2193', inplace=True)
pt_demand.set_crs('epsg:2193', inplace=True)
hybrid_services.to_crs(crs=2193, inplace=True)

In [5]:
#create geodataframe of all road geometries in Tauranga

gdf = ox.graph_to_gdfs(G, nodes=False, edges=True)

In [6]:
gdf.head()

osmid   lanes   
u         v          key                                               
247014753 7397434438 0                             657538168       2  \
          4866204635 0    [701547512, 461219596, 1107883893]  [2, 1]   
247014899 247014903  0                [1103106292, 27212758]  [1, 3]   
          1597355601 0                             146443707       2   
247014903 298632431  0                             392378544     NaN   

                                       name    highway maxspeed  oneway   
u         v          key                                                  
247014753 7397434438 0      Te Puke Highway  secondary      100   False  \
          4866204635 0                  NaN  secondary       70    True   
247014899 247014903  0    State Highway 29A      trunk       50    True   
          1597355601 0    State Highway 29A      trunk      100   False   
247014903 298632431  0                  NaN      trunk       50    True   

                         reversed    length   
u         v          key                      
247014753 7397434438 0       True   585.773  \
          4866204635 0      False   123.800   
247014899 247014903  0      False   349.942   
          1597355601 0       True  1351.773   
247014903 298632431  0      False    12.105   

                                                                   geometry   
u         v          key                                                      
247014753 7397434438 0    LINESTRING (176.28407 -37.71666, 176.28416 -37...  \
          4866204635 0    LINESTRING (176.28407 -37.71666, 176.28393 -37...   
247014899 247014903  0    LINESTRING (176.17417 -37.72352, 176.17384 -37...   
          1597355601 0    LINESTRING (176.17417 -37.72352, 176.17432 -37...   
247014903 298632431  0    LINESTRING (176.17059 -37.72473, 176.17046 -37...   

                             ref bridge  junction width area access  
u         v          key                                             
247014753 7397434438 0       NaN    NaN       NaN   NaN  NaN    NaN  
          4866204635 0       NaN    NaN       NaN   NaN  NaN    NaN  
247014899 247014903  0    SH 29A    NaN       NaN   NaN  NaN    NaN  
          1597355601 0    SH 29A    NaN       NaN   NaN  NaN    NaN  
247014903 298632431  0    SH 29A    yes  circular   NaN  NaN    NaN

In [7]:
#drop na values from gdf column'lanes', set CRS

gdf_drop = gdf.dropna(subset=['lanes'])
gdf_drop.head()
gdf_drop.set_crs('epsg:2193', inplace=True, allow_override=True)

C:\Users\GSE1\.conda\envs\ox\Lib\site-packages\geopandas\geodataframe.py:1443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


osmid   lanes   
u           v           key                                               
247014753   7397434438  0                             657538168       2  \
            4866204635  0    [701547512, 461219596, 1107883893]  [2, 1]   
247014899   247014903   0                [1103106292, 27212758]  [1, 3]   
            1597355601  0                             146443707       2   
247014956   3777941155  0                             374405015       3   
...                                                         ...     ...   
10235183745 9499693321  0                             755863781       1   
10235183746 10235183752 0                             755863780       1   
10235183752 7059762011  0                             755863780       1   
10235183753 10235183745 0                             755863781       1   
10235226142 10145438695 0                            1119121977       2   

                                          name    highway maxspeed  oneway   
u           v           key                                                  
247014753   7397434438  0      Te Puke Highway  secondary      100   False  \
            4866204635  0                  NaN  secondary       70    True   
247014899   247014903   0    State Highway 29A      trunk       50    True   
            1597355601  0    State Highway 29A      trunk      100   False   
247014956   3777941155  0    State Highway 29A      trunk       50    True   
...                                        ...        ...      ...     ...   
10235183745 9499693321  0      Te Okuroa Drive  secondary       50    True   
10235183746 10235183752 0      Te Okuroa Drive  secondary       50    True   
10235183752 7059762011  0      Te Okuroa Drive  secondary       50    True   
10235183753 10235183745 0      Te Okuroa Drive  secondary       50    True   
10235226142 10145438695 0      Taurikura Drive  secondary      NaN    True   

                            reversed    length   
u           v           key                      
247014753   7397434438  0       True   585.773  \
            4866204635  0      False   123.800   
247014899   247014903   0      False   349.942   
            1597355601  0       True  1351.773   
247014956   3777941155  0      False    38.873   
...                              ...       ...   
10235183745 9499693321  0      False   171.369   
10235183746 10235183752 0      False     8.612   
10235183752 7059762011  0      False    24.754   
10235183753 10235183745 0      False     8.458   
10235226142 10145438695 0      False    26.442   

                                                                      geometry   
u           v           key                                                      
247014753   7397434438  0    LINESTRING (176.284 -37.717, 176.284 -37.717, ...  \
            4866204635  0    LINESTRING (176.284 -37.717, 176.284 -37.717, ...   
247014899   247014903   0    LINESTRING (176.174 -37.724, 176.174 -37.724, ...   
            1597355601  0    LINESTRING (176.174 -37.724, 176.174 -37.723, ...   
247014956   3777941155  0    LINESTRING (176.168 -37.727, 176.168 -37.727, ...   
...                                                                        ...   
10235183745 9499693321  0    LINESTRING (176.348 -37.731, 176.347 -37.731, ...   
10235183746 10235183752 0        LINESTRING (176.348 -37.731, 176.348 -37.731)   
10235183752 7059762011  0        LINESTRING (176.348 -37.731, 176.348 -37.731)   
10235183753 10235183745 0        LINESTRING (176.348 -37.731, 176.348 -37.731)   
10235226142 10145438695 0    LINESTRING (176.087 -37.756, 176.087 -37.756, ...   

                                ref bridge junction width area access  
u           v           key                                            
247014753   7397434438  0       NaN    NaN      NaN   NaN  NaN    NaN  
            4866204635  0       NaN    NaN      NaN   NaN  NaN    NaN  
247014899   247014903   0    SH 29A    NaN      NaN   NaN  Na

In [8]:
# filter by lanes and include 'oneway' only

two_lane = gdf_drop.loc[(gdf_drop['lanes']=='2')&(gdf_drop['oneway']=='True')]
three_lane = gdf_drop.loc[(gdf_drop['lanes']=='3')&(gdf_drop['oneway']=='True')] 
four_lane = gdf_drop.loc[(gdf_drop['lanes']=='4')&(gdf_drop['oneway']=='True')] 
five_lane = gdf_drop.loc[(gdf_drop['lanes']=='5')&(gdf_drop['oneway']=='True')] 

In [9]:
# filter junctions

junction_circular = gdf_drop.loc[(gdf_drop['junction']=='circular')]
junction_roundabout = gdf_drop.loc[(gdf_drop['junction']=='roundabout')]

In [10]:
# filter by segment length: bus lane=0-25m,BRT=500m+, Busway=500m+ 

bus_lane = gdf_drop.loc[(gdf_drop['lanes']=='2')|(gdf_drop['lanes']=="['3','2']")&(gdf_drop['oneway']==True)]
brt = gdf_drop.loc[(gdf_drop['lanes']=='2')&(gdf_drop['oneway']==True)&(gdf_drop['length']>=500)]
busway = gdf_drop.loc[(gdf_drop['lanes']=='3')&(gdf_drop['oneway']==True)&(gdf_drop['length']>=500)]

In [11]:
#pt demand - drop all columns except PT and geometry. Set CRS

pt_demand = pt_demand.loc[:, ['ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT', 'geometry']]

In [12]:
pt_demand.columns

Index(['ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT', 'geometry'], dtype='object')

In [13]:
# change data types of columns to float

pt_demand[['ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT']] = pt_demand[['ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT']].astype(float)

In [14]:
# Create equal-sized bins of AM PT demand and create new column
pt_demand['PT_BIN'] = pd.cut(pt_demand['AM_PT'], bins=5, labels=False)

In [15]:
pt_demand['AM_PT'].describe()

count    5610.000000
mean       21.936649
std        51.931386
min         0.000000
25%         0.000000
50%         0.000000
75%        15.727500
max       432.620000
Name: AM_PT, dtype: float64

In [16]:
hybrid_services['vehicle_co'].describe()

count    13.000000
mean     12.230769
std       8.237656
min       3.000000
25%       5.000000
50%      11.000000
75%      20.000000
max      27.000000
Name: vehicle_co, dtype: float64

In [17]:
pt_demand.describe()

ADT_PUBLIC       ADT_PT        AM_PT        IP_PT        PM_PT   
count  5610.000000  5610.000000  5610.000000  5610.000000  5610.000000  \
mean     90.735478   120.726964    21.936649     7.877201     7.597679   
std     273.936880   304.096187    51.931386    21.665912    25.045798   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%      42.661130    79.052500    15.727500     4.610000     2.140000   
max    2552.208250  2590.752930   432.620000   201.080000   289.710000   

            PT_BIN  
count  5610.000000  
mean      0.134403  
std       0.481177  
min       0.000000  
25%       0.000000  
50%       0.000000  
75%       0.000000  
max       4.000000

In [18]:
# only show links with demand higher than 75th percentile

high_pt = pt_demand.loc[(pt_demand['AM_PT']>16)]

In [19]:
high_pt.head()

ADT_PUBLIC     ADT_PT   AM_PT  IP_PT  PM_PT   
694     0.00000  177.48000   69.91   5.38   0.00  \
695     0.00000  181.66000   38.82  14.86   0.00   
696     0.00000  181.66000   38.82  14.86   0.00   
697   360.85474  551.50476  151.92  27.14  19.70   
699   353.31174  654.24176  103.59  50.30  33.23   

                                              geometry  PT_BIN  
694  MULTILINESTRING ((1873784.000 5818987.000, 187...       0  
695  MULTILINESTRING ((1873784.000 5818987.000, 187...       0  
696  MULTILINESTRING ((1873882.000 5819037.000, 187...       0  
697  MULTILINESTRING ((1873882.000 5819037.000, 187...       1  
699  MULTILINESTRING ((1873882.000 5819037.000, 187...       1

In [20]:
high_vehicle = hybrid_services.loc[(hybrid_services['vehicle_co']>=11)]

In [41]:
high_vehicle.shape

(7, 20)

In [22]:
high_pt_bin = pt_demand.loc[(pt_demand['PT_BIN']>=1)]

In [23]:
high_pt_bin['AM_PT'].describe()

count    517.000000
mean     160.090619
std       73.096333
min       86.650000
25%      105.890000
50%      140.340000
75%      196.220000
max      432.620000
Name: AM_PT, dtype: float64

In [24]:
los_nodes_am.columns

Index(['N', 'DELAY_MAX', 'LOS_MAX', 'DELAY_WAVG', 'LOS_WAVG', 'SECTOR', 'X',
       'Y', 'LOCATION', 'LABEL', 'FAREZONE', 'geometry'],
      dtype='object')

In [25]:
low_los_nodes = los_nodes_am.loc[(los_nodes_am['LOS_WAVG']>=3)]
low_los_links = los_links_am.loc[(los_links_am['LOS']>=3)]

In [61]:
# Folium map

m = high_pt_bin.explore(column="AM_PT",
    tiles="CartoDB positron",
    tooltip="AM_PT",
    highlight=True,
    name='AM peak PT Demand',
    k=5,
    popup=['AM_PT'])

buses = high_vehicle.explore(
    m=m,
    column="vehicle_co",
    tooltip="line_name",
    name="Hybrid Network Bus Routes",
    highlight=True)


los_nodes = low_los_nodes.explore(
    m=m,
    column="LOS_WAVG",
    tooltip="LOS_WAVG",
    name="LOS Nodes (AM)",
    highlight=True,
    marker_type="circle_marker",
    marker_kwds={
        "radius" : "6"})

los_links = low_los_links.explore(
    m=m,
    column="LOS",
    tooltip="LOS",
    name="LOS Links (AM)",
    highlight=True,)

folium.LayerControl().add_to(m)

m

In [44]:
priority_links = high_pt_bin.sjoin(high_vehicle, how="left")

In [45]:
priority_links.explore()

In [46]:
pt_priority_intersection = priority_links.overlay(low_los_nodes, how='intersection', keep_geom_type=False)

In [62]:
pt_priority_intersection.explore()

In [49]:
pt_priority_intersection.columns

Index(['ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT', 'PT_BIN',
       'index_right', 'full_name', 'dir_id', 'dir_name', 'pattern', 'line_id',
       'line_name', 'line_color', 'map_id', 'map_name', 'url', 'km',
       'hours_year', 'cost_year', 'vehicle_ty', 'vehicle_co', 'minheadway',
       'maxheadway', 'minkph', 'maxkph', 'N', 'DELAY_MAX', 'LOS_MAX',
       'DELAY_WAVG', 'LOS_WAVG', 'SECTOR', 'X', 'Y', 'LOCATION', 'LABEL',
       'FAREZONE', 'geometry'],
      dtype='object')

In [64]:
pt_priority_intersection = pt_priority_intersection.dropna(subset=['vehicle_co'])

In [65]:
# rank nodes based on demand

pt_priority_intersection['rank'] = pt_priority_intersection['vehicle_co'].rank(method="average", ascending=False).astype('int')

In [66]:
pt_priority_intersection.head()

ADT_PUBLIC      ADT_PT   AM_PT   IP_PT  PM_PT  PT_BIN  index_right   
12   244.75258   472.17258  197.67    8.22   6.60       2          9.0  \
16     0.00000   392.06000  145.91   14.32   0.00       1          4.0   
23   842.53601  1218.24597  249.65   85.55  40.68       2          4.0   
25   899.13450  1291.91450  157.34  102.98  89.79       1          4.0   
27   842.53601  1218.24597  249.65   85.55  40.68       2          4.0   

                                         full_name      dir_id dir_name  ...   
12                  L Omokoroa - Airport - inbound  1190326851  inbound  ...  \
16  A Mt Maunganui - City - Tauriko West - inbound  1190326829  inbound  ...   
23  A Mt Maunganui - City - Tauriko West - inbound  1190326829  inbound  ...   
25  A Mt Maunganui - City - Tauriko West - inbound  1190326829  inbound  ...   
27  A Mt Maunganui - City - Tauriko West - inbound  1190326829  inbound  ...   

   DELAY_WAVG LOS_WAVG SECTOR          X          Y LOCATION         LABEL   
12   25.37175        3      0  1872695.0  5823051.0        0        Minden  \
16   22.44823        3      0  1877033.0  5821374.0        0  Cameron/23th   
23   21.85969        3      0  1877639.0  5821914.0        0  Cameron/18th   
25   21.85969        3      0  1877639.0  5821914.0        0  Cameron/18th   
27   27.86193        3      0  1877811.0  5822074.0        0  Cameron/17th   

    FAREZONE                         geometry  rank  
12         2  POINT (1872695.000 5823051.000)   123  
16         2  POINT (1877033.000 5821374.000)    84  
23         2  POINT (1877639.000 5821914.000)    84  
25         2  POINT (1877639.000 5821914.000)    84  
27         2  POINT (1877811.000 5822074.000)    84  

[5 rows x 39 columns]

In [69]:
#identify links where there is high PT demand and high number of buses

links_merged = high_pt_bin.sjoin(high_vehicle, how="left")

In [70]:
pt_priority_links = low_los_links.overlay(links_merged, how='intersection', keep_geom_type=True)

In [71]:
pt_priority_links.columns

Index(['A', 'B', 'FREIGHTLANE', 'BUSLANE', 'BL_IP', 'GRADIENT', 'FSFACTOR',
       'DISTANCE', 'LINKTYPE', 'JURISDICT', 'CAPINDEX', 'TSFLAG', 'HOVLANE',
       'ORG_CAP', 'MOD_CAP', 'SCHEME', 'DEL', 'LANEOP', 'ORG_FSPD', 'MOD_FSPD',
       'AKCEJ', 'LANENUM', 'TOLLENTRY', 'TOLLEXIT', 'TOLLROAD', 'TOLL',
       'HCVTOLL', 'IPFACTOR', 'LINKTAG', 'CAPACITY', 'FSPEED', 'CALDIS',
       'DIFFDIS', 'V_1', 'TIME_1', 'VC_1', 'CSPD_1', 'VDT_1', 'VHT_1', 'V1_1',
       'V2_1', 'V3_1', 'V4_1', 'V5_1', 'V6_1', 'V7_1', 'V8_1', 'V9_1', 'V10_1',
       'V11_1', 'V12_1', 'V13_1', 'V14_1', 'VT_1', 'V1T_1', 'V2T_1', 'V3T_1',
       'V4T_1', 'V5T_1', 'V6T_1', 'V7T_1', 'V8T_1', 'V9T_1', 'V10T_1',
       'V11T_1', 'V12T_1', 'V13T_1', 'V14T_1', 'LW_TTIME_1', 'TYPE', 'LOS',
       'ADT_PUBLIC', 'ADT_PT', 'AM_PT', 'IP_PT', 'PM_PT', 'PT_BIN',
       'index_right', 'full_name', 'dir_id', 'dir_name', 'pattern', 'line_id',
       'line_name', 'line_color', 'map_id', 'map_name', 'url', 'km',
       'hours_year', '

In [76]:
pt_priority_links = pt_priority_links.dropna(subset=['vehicle_co'])

In [77]:
pt_priority_links['rank'] = pt_priority_links['vehicle_co'].rank(method="average", ascending=False).astype('int')

In [84]:
pt_priority_intersection.shape

(134, 39)

In [85]:
pt_priority_links.shape

(340, 99)

# What happens when you prioritise investment to impact more bus movements?

In [86]:
map = pt_priority_intersection.explore(tiles="CartoDB positron",
    column="rank",
    tooltip=['AM_PT', 'LOS_WAVG', "rank"],
    highlight=True,
    name="Nodes",
    marker_type="circle_marker",
    marker_kwds={
        "radius" : "6"},
    legend_kwds= {
        "caption" : "Nodes by priority rank"
    },
    cmap='viridis')

links = pt_priority_links.explore(
    m=map,
    column="rank",
    tooltip=["AM_PT", "LOS", "rank"],
    highlight=True,
    name="Links",
    legend_kwds= {
        "caption" : "Links by priority rank"
    })

folium.LayerControl().add_to(map)

map

In [88]:
pt_priority_links.to_excel('ip_links_bus_threshold.xlsx')